In [72]:
import pandas as pd
import matplotlib
import os
#주소값을 위도 경도로 바꿔주는 라이브러리
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter
import googlemaps
from time import sleep

print(pd.__version__)
print(matplotlib.__version__)

2.2.2
3.8.4


### Extract한 총기 사건 데이터 csv 가져오기

In [73]:
# 폴더 경로 설정
folder_path = 'new_orleans_csv/'

# 폴더 안의 모든 CSV 파일 목록 가져오기
csv_files = [file for file in os.listdir(folder_path) if file.endswith('.csv')]

total_df = pd.DataFrame()

# CSV 파일들을 순차적으로 읽어서 데이터프레임에 병합
for csv_file in csv_files:
    file_path = os.path.join(folder_path, csv_file)
    temp_df = pd.read_csv(file_path)
    total_df = pd.concat([total_df, temp_df], ignore_index=True)

# 병합된 데이터프레임 출력
total_df

Incident ID      Incident Date      State City Or County  \
0          273662  December 31, 2014  Louisiana    New Orleans   
1          272337  December 31, 2014  Louisiana    New Orleans   
2          272335  December 31, 2014  Louisiana    New Orleans   
3          272378  December 30, 2014  Louisiana    New Orleans   
4          270684  December 29, 2014  Louisiana    New Orleans   
...           ...                ...        ...            ...   
6651      2849634           1.Jan.23  Louisiana    New Orleans   
6652      2495947           1.Jan.23  Louisiana    New Orleans   
6653      2495945           1.Jan.23  Louisiana    New Orleans   
6654      2492983           1.Jan.23  Louisiana    New Orleans   
6655      2492985           1.Jan.23  Louisiana    New Orleans   

                                        Address  Victims Killed  \
0                 Bullard Avenue and Dwyer Road               0   
1     S Derbigny St and Martin Luther King Blvd               0   
2                  Curran Rd and Shorewood Blvd               0   
3              Pauger and North Villere streets               0   
4                       First and Clara streets               0   
...                                         ...             ...   
6651             6000 block of Chef Menteur Hwy               0   
6652                    Downman Rd and Dwyer Rd               0   
6653                                        NaN               0   
6654                      1600 block of Clio St               1   
6655                   4000 block of Tulane Ave               0   

      Victims Injured  Suspects Killed  Suspects Injured  Suspects Arrested  \
0                   0                0                 0                  1   
1                   1                0                 0                  0   
2                   1                0                 0                  0   
3                   1                0                 0                  0   
4                   2                0                 0                  0   
...               ...              ...               ...                ...   
6651                1                0                 0                  0   
6652                1                0                 0                  0   
6653                1                0                 0                  0   
6654                0                0                 0                  1   
6655                0                0                 1                  0   

      Operations  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  
...          ...  
6651         NaN  
6652         NaN  
6653         NaN  
6654         NaN  
6655         NaN  

[6656 rows x 11 columns]

### 칼럼이름 재설정 (띄워쓰기 제거)

In [74]:
#칼럼이름 띄워쓰기 제거하고 이름 재설정해줌
total_df = total_df.rename(columns={'Incident ID':'IncidentID'}) 
total_df = total_df.rename(columns={'Incident Date':'IncidentDate'}) 
total_df = total_df.rename(columns={'City Or County':'City_or_Country'})
total_df = total_df.rename(columns={'Victims Killed':'Victims_Killed'})
total_df = total_df.rename(columns={'Victims Injured':'Victims_Injured'})
total_df = total_df.rename(columns={'Suspects Killed':'Suspects_Killed'})
total_df = total_df.rename(columns={'Suspects Injured':'Suspects_Injured'})
total_df = total_df.rename(columns={'Suspects Arrested':'Suspects_Arrested'})

### 유효하지 않은 주소 값(Nan) 제외하기

In [75]:
date_error = total_df[total_df['Address'].isna()]
date_error

IncidentID        IncidentDate      State City_or_Country Address  \
93        221597    October 28, 2014  Louisiana     New Orleans     NaN   
120       205446    October 13, 2014  Louisiana     New Orleans     NaN   
146       194530  September 21, 2014  Louisiana     New Orleans     NaN   
201       178477     August 18, 2014  Louisiana     New Orleans     NaN   
206       178486     August 16, 2014  Louisiana     New Orleans     NaN   
...          ...                 ...        ...             ...     ...   
6360     2610797           27.May.23  Louisiana     New Orleans     NaN   
6593     2514270           29.Jan.23  Louisiana     New Orleans     NaN   
6615     2849744           16.Jan.23  Louisiana     New Orleans     NaN   
6635     2498930            5.Jan.23  Louisiana     New Orleans     NaN   
6653     2495945            1.Jan.23  Louisiana     New Orleans     NaN   

      Victims_Killed  Victims_Injured  Suspects_Killed  Suspects_Injured  \
93                 0                0                0                 0   
120                0                1                0                 0   
146                0                1                0                 0   
201                0                1                0                 0   
206                0                1                0                 0   
...              ...              ...              ...               ...   
6360               0                1                0                 0   
6593               0                1                0                 0   
6615               0                1                0                 0   
6635               1                0                0                 0   
6653               0                1                0                 0   

      Suspects_Arrested  Operations  
93                    0         NaN  
120                   0         NaN  
146                   0         NaN  
201                   0         NaN  
206                   0         NaN  
...                 ...         ...  
6360                  0         NaN  
6593                  0         NaN  
6615                  0         NaN  
6635                  0         NaN  
6653                  0         NaN  

[110 rows x 11 columns]

In [76]:
# 주소가 없는 행을 삭제
total_df = total_df.dropna(subset=['Address'])

### 모든 날짜를 동일 형식으로 변환 후 추가 (Timestamp)

In [77]:
# 여러 날짜 형식을 처리하기 위한 함수 정의
def convert_date(date_str):
    # 시도할 날짜 형식들
    formats = ['%B %d, %Y', '%Y-%m-%d', '%d.%b.%y']
    for fmt in formats:
        try:
            # 주어진 형식으로 날짜 변환 시도
            return pd.to_datetime(date_str, format=fmt)
        except ValueError:
            continue
    # 변환 실패 시 NaT 반환
    return pd.NaT

# Incident Date 칼럼에 날짜 변환 함수 적용
total_df['Timestamp'] = total_df['IncidentDate'].apply(convert_date)
total_df['Timestamp'] = total_df['Timestamp'].dt.strftime('%Y-%m-%d')

# 결과 출력
total_df


IncidentID       IncidentDate      State City_or_Country  \
0         273662  December 31, 2014  Louisiana     New Orleans   
1         272337  December 31, 2014  Louisiana     New Orleans   
2         272335  December 31, 2014  Louisiana     New Orleans   
3         272378  December 30, 2014  Louisiana     New Orleans   
4         270684  December 29, 2014  Louisiana     New Orleans   
...          ...                ...        ...             ...   
6650     2494793           2.Jan.23  Louisiana     New Orleans   
6651     2849634           1.Jan.23  Louisiana     New Orleans   
6652     2495947           1.Jan.23  Louisiana     New Orleans   
6654     2492983           1.Jan.23  Louisiana     New Orleans   
6655     2492985           1.Jan.23  Louisiana     New Orleans   

                                        Address  Victims_Killed  \
0                 Bullard Avenue and Dwyer Road               0   
1     S Derbigny St and Martin Luther King Blvd               0   
2                  Curran Rd and Shorewood Blvd               0   
3              Pauger and North Villere streets               0   
4                       First and Clara streets               0   
...                                         ...             ...   
6650                       I-10 and Orleans Ave               0   
6651             6000 block of Chef Menteur Hwy               0   
6652                    Downman Rd and Dwyer Rd               0   
6654                      1600 block of Clio St               1   
6655                   4000 block of Tulane Ave               0   

      Victims_Injured  Suspects_Killed  Suspects_Injured  Suspects_Arrested  \
0                   0                0                 0                  1   
1                   1                0                 0                  0   
2                   1                0                 0                  0   
3                   1                0                 0                  0   
4                   2                0                 0                  0   
...               ...              ...               ...                ...   
6650                1                0                 0                  0   
6651                1                0                 0                  0   
6652                1                0                 0                  0   
6654                0                0                 0                  1   
6655                0                0                 1                  0   

      Operations   Timestamp  
0            NaN  2014-12-31  
1            NaN  2014-12-31  
2            NaN  2014-12-31  
3            NaN  2014-12-30  
4            NaN  2014-12-29  
...          ...         ...  
6650         NaN  2023-01-02  
6651         NaN  2023-01-01  
6652         NaN  2023-01-01  
6654         NaN  2023-01-01  
6655         NaN  2023-01-01  

[6546 rows x 12 columns]

In [78]:
# 타임스탬프가 NaN인 행을 확인
timestamp_error = total_df[total_df['Timestamp'].isna()]
timestamp_error

Empty DataFrame
Columns: [IncidentID, IncidentDate, State, City_or_Country, Address, Victims_Killed, Victims_Injured, Suspects_Killed, Suspects_Injured, Suspects_Arrested, Operations, Timestamp]
Index: []

### 위도, 경도 값 반환 후 추가

In [79]:
# Google Maps 클라이언트 초기화
api_key = 'Your Google Maps API Key' 
gmaps = googlemaps.Client(key=api_key)

latitudes = []
longitudes = []

# 기존 데이터 프레임의 Adress,state,city or coubtry 값을 기반으로 위도 경도 찾기
for idx, row in total_df.iterrows():
    address = f"{row['Address']}, {row['City_or_Country']}, {row['State']}"
    try:
        geocode_result = gmaps.geocode(address)
        print(geocode_result)
        if geocode_result:
            location = geocode_result[0]['geometry']['location']
            latitudes.append(location['lat'])
            longitudes.append(location['lng'])
        else:
            latitudes.append(None)
            longitudes.append(None)
    except Exception as e:
        latitudes.append(None)
        longitudes.append(None)

# 결과를 데이터프레임에 추가
total_df['Latitude'] = latitudes
total_df['Longitude'] = longitudes


print(total_df.head())

# 위도,경도 값 반환되지 않은 행 필터링
trans_address_error = total_df[total_df['Latitude'].isna() & total_df['Longitude'].isna()]

# 
#print(trans_address_error)

[{'address_components': [{'long_name': 'Dwyer Road & Bullard Avenue', 'short_name': 'Dwyer Rd & Bullard Ave', 'types': ['intersection']}, {'long_name': 'New Orleans East Area', 'short_name': 'New Orleans East Area', 'types': ['neighborhood', 'political']}, {'long_name': 'New Orleans', 'short_name': 'New Orleans', 'types': ['locality', 'political']}, {'long_name': 'Orleans Parish', 'short_name': 'Orleans Parish', 'types': ['administrative_area_level_2', 'political']}, {'long_name': 'Louisiana', 'short_name': 'LA', 'types': ['administrative_area_level_1', 'political']}, {'long_name': 'United States', 'short_name': 'US', 'types': ['country', 'political']}, {'long_name': '70128', 'short_name': '70128', 'types': ['postal_code']}], 'formatted_address': 'Dwyer Rd & Bullard Ave, New Orleans, LA 70128, USA', 'geometry': {'location': {'lat': 30.0287245, 'lng': -89.9478391}, 'location_type': 'GEOMETRIC_CENTER', 'viewport': {'northeast': {'lat': 30.0300734802915, 'lng': -89.94649011970849}, 'south

In [56]:
# 위도, 경도 반환 안되서 nan값인거 확인
trans_address_error = total_df[total_df['Latitude'].isna() & total_df['Longitude'].isna()]
trans_address_error

Empty DataFrame
Columns: [IncidentID, IncidentDate, State, City_or_Country, Address, Victims_Killed, Victims_Injured, Suspects_Killedd, Suspects_Injured, Suspects_Arrested, Operations, Timestamp, Latitude, Longitude]
Index: []

In [70]:
total_df

IncidentID       IncidentDate      State City_or_Country  \
0         273662  December 31, 2014  Louisiana     New Orleans   
1         272337  December 31, 2014  Louisiana     New Orleans   
2         272335  December 31, 2014  Louisiana     New Orleans   
3         272378  December 30, 2014  Louisiana     New Orleans   
4         270684  December 29, 2014  Louisiana     New Orleans   
...          ...                ...        ...             ...   
6650     2494793           2.Jan.23  Louisiana     New Orleans   
6651     2849634           1.Jan.23  Louisiana     New Orleans   
6652     2495947           1.Jan.23  Louisiana     New Orleans   
6654     2492983           1.Jan.23  Louisiana     New Orleans   
6655     2492985           1.Jan.23  Louisiana     New Orleans   

                                        Address  Victims_Killed  \
0                 Bullard Avenue and Dwyer Road               0   
1     S Derbigny St and Martin Luther King Blvd               0   
2                  Curran Rd and Shorewood Blvd               0   
3              Pauger and North Villere streets               0   
4                       First and Clara streets               0   
...                                         ...             ...   
6650                       I-10 and Orleans Ave               0   
6651             6000 block of Chef Menteur Hwy               0   
6652                    Downman Rd and Dwyer Rd               0   
6654                      1600 block of Clio St               1   
6655                   4000 block of Tulane Ave               0   

      Victims_Injured  Suspects_Killed  Suspects_Injured  Suspects_Arrested  \
0                   0                0                 0                  1   
1                   1                0                 0                  0   
2                   1                0                 0                  0   
3                   1                0                 0                  0   
4                   2                0                 0                  0   
...               ...              ...               ...                ...   
6650                1                0                 0                  0   
6651                1                0                 0                  0   
6652                1                0                 0                  0   
6654                0                0                 0                  1   
6655                0                0                 1                  0   

      Operations   Timestamp   Latitude  Longitude  
0            NaN  2014-12-31  30.028724 -89.947839  
1            NaN  2014-12-31  29.946854 -90.089523  
2            NaN  2014-12-31  30.068463 -89.946724  
3            NaN  2014-12-30  29.971366 -90.060650  
4            NaN  2014-12-29  29.939518 -90.096374  
...          ...         ...        ...        ...  
6650         NaN  2023-01-02  30.412899 -91.455678  
6651         NaN  2023-01-01  30.009018 -90.019145  
6652         NaN  2023-01-01  30.018341 -90.021611  
6654         NaN  2023-01-01  29.941336 -90.073811  
6655         NaN  2023-01-01  29.967969 -90.105522  

[6546 rows x 14 columns]

### 변환된 데이터 프레임 csv파일로 저장

In [71]:
total_df.to_csv('Gun_Violence_Transform_Result.csv',index=False)